***
***
# 使用GraphLab进行音乐推荐
***
***


In [1]:
import graphlab as gl
# set canvas to show sframes and sgraphs in ipython notebook
gl.canvas.set_target('ipynb')

[INFO] graphlab.cython.cy_server: GraphLab Create v2.1 started. Logging: /tmp/graphlab_server_1525500461.log


This non-commercial license of GraphLab Create for academic use is assigned to wangchengjun@nju.edu.cn and will expire on March 14, 2019.


# 下载数据
http://s3.amazonaws.com/dato-datasets/millionsong/10000.txt


In [10]:
#train_file = 'http://s3.amazonaws.com/dato-datasets/millionsong/10000.txt'
train_file = '/Users/datalab/bigdata/cjc/millionsong/song_usage_10000.txt'
sf = gl.SFrame.read_csv(train_file, header=False, delimiter='\t', verbose=False)
sf.rename({'X1':'user_id', 'X2':'music_id', 'X3':'rating'})

Columns:
	user_id	str
	music_id	str
	rating	int

Rows: 2000000

Data:
+-------------------------------+--------------------+--------+
|            user_id            |      music_id      | rating |
+-------------------------------+--------------------+--------+
| b80344d063b5ccb3212f76538f... | SOAKIMP12A8C130995 |   1    |
| b80344d063b5ccb3212f76538f... | SOBBMDR12A8C13253B |   2    |
| b80344d063b5ccb3212f76538f... | SOBXHDL12A81C204C0 |   1    |
| b80344d063b5ccb3212f76538f... | SOBYHAJ12A6701BF1D |   1    |
| b80344d063b5ccb3212f76538f... | SODACBL12A8C13C273 |   1    |
| b80344d063b5ccb3212f76538f... | SODDNQT12A6D4F5F7E |   5    |
| b80344d063b5ccb3212f76538f... | SODXRTY12AB0180F3B |   1    |
| b80344d063b5ccb3212f76538f... | SOFGUAY12AB017B0A8 |   1    |
| b80344d063b5ccb3212f76538f... | SOFRQTD12A81C233C0 |   1    |
| b80344d063b5ccb3212f76538f... | SOHQWYZ12A6D4FA701 |   1    |
+-------------------------------+--------------------+--------+
[2000000 rows x 3 columns]
Note: Only the head of the SFrame is printed.
You can use print_rows(num_rows=m, num_columns=n) to print more rows and columns.

In [11]:
train_set, test_set = sf.random_split(0.8, seed=1)

In [12]:
popularity_model = gl.popularity_recommender.create(train_set, 
                                                    'user_id', 'music_id', 
                                                    target = 'rating')

Recsys training: model = popularity

Preparing data set.

Data has 1599753 observations with 76085 users and 10000 items.

Data prepared in: 1.2441s

1599753 observations to process; with 10000 unique items.

In [13]:
item_sim_model = gl.item_similarity_recommender.create(train_set, 
                                                       'user_id', 'music_id', 
                                                       target = 'rating', 
                                                       similarity_type='cosine')

Recsys training: model = item_similarity

Preparing data set.

Data has 1599753 observations with 76085 users and 10000 items.

Data prepared in: 1.18984s

Training model from provided data.

...

| 994.743ms                           | 100              | 10000           |

+-------------------------------------+------------------+-----------------+

Finalizing lookup tables.

Generating candidate set for working with new users.

Finished training in 1.06117s

In [14]:
factorization_machine_model = gl.recommender.factorization_recommender.create(train_set, 
                                                                              'user_id', 'music_id',
                                                                              target='rating')

Recsys training: model = factorization_recommender

Preparing data set.

Data has 1599753 observations with 76085 users and 10000 items.

Data prepared in: 1.21379s

Training factorization_recommender for recommendations.

...

+---------+--------------+-------------------+-----------------------+-------------+

Optimization Complete: Maximum number of passes through the data reached.

Computing final objective value and training RMSE.

Final objective value: 9.81513

Final training RMSE: 3.1314

In [17]:
len(train_set)

1599753

In [16]:
result = gl.recommender.util.compare_models(test_set, 
                                            [popularity_model, item_sim_model, factorization_machine_model],
                                            user_sample=.5, skip_set=train_set)

compare_models: using 34355 users to estimate model performance
PROGRESS: Evaluate model M0


recommendations finished on 1000/34355 queries. users per second: 18058.4

recommendations finished on 2000/34355 queries. users per second: 21323.8

recommendations finished on 3000/34355 queries. users per second: 22068.6

recommendations finished on 4000/34355 queries. users per second: 22236.7

...

recommendations finished on 31000/34355 queries. users per second: 20777.4

recommendations finished on 32000/34355 queries. users per second: 20721.2

recommendations finished on 33000/34355 queries. users per second: 20763

recommendations finished on 34000/34355 queries. users per second: 20792.3


Precision and recall summary statistics by cutoff
+--------+-------------------+-------------------+
| cutoff |   mean_precision  |    mean_recall    |
+--------+-------------------+-------------------+
|   1    | 0.000436617668462 | 8.84193897883e-05 |
|   2    | 0.000392955901615 | 0.000146983613211 |
|   3    | 0.000397807209043 | 0.000273528343889 |
|   4    | 0.000400232862757 | 0.000328267207427 |
|   5    | 0.000424974530636 |  0.00040585165237 |
|   6    | 0.000460874205598 | 0.000574532683748 |
|   7    |  0.00049483335759 | 0.000721448772082 |
|   8    | 0.000531218163295 | 0.000887467388127 |
|   9    |  0.00055628325167 |  0.00109888572439 |
|   10   | 0.000593800029108 |  0.00130662212516 |
+--------+-------------------+-------------------+
[10 rows x 3 columns]

('\nOverall RMSE: ', 8.111262615677196)

Per User RMSE (best)
+-------------------------------+-------+-------------------+
|            user_id            | count |        rmse       |
+-------------------------

In [8]:
K = 10
users = gl.SArray(sf['user_id'].unique().head(100))

In [9]:
recs = item_sim_model.recommend(users=users, k=K)
recs.head()

Columns:
	user_id	str
	music_id	str
	score	float
	rank	int

Rows: 10

Data:
+-------------------------------+--------------------+----------------+------+
|            user_id            |      music_id      |     score      | rank |
+-------------------------------+--------------------+----------------+------+
| 279292bb36dbfc7f505e36ebf0... | SOXUQNR12AF72A69D6 | 3.02242265145  |  1   |
| 279292bb36dbfc7f505e36ebf0... | SOUFAZA12AC3DFAB20 | 1.33684277534  |  2   |
| 279292bb36dbfc7f505e36ebf0... | SOSFSTC12A8C141219 | 1.09198212624  |  3   |
| 279292bb36dbfc7f505e36ebf0... | SOVIWFP12A58A7D1BD | 1.04516386986  |  4   |
| 279292bb36dbfc7f505e36ebf0... | SOBMTQD12AB01833D0 | 1.02945168813  |  5   |
| 279292bb36dbfc7f505e36ebf0... | SOCMNRG12AB0189D3F | 0.975643793742 |  6   |
| 279292bb36dbfc7f505e36ebf0... | SOXOHUM12A67ADC826 | 0.950687328974 |  7   |
| 279292bb36dbfc7f505e36ebf0... | SOWBFVW12A6D4F612B | 0.909237066905 |  8   |
| 279292bb36dbfc7f505e36ebf0... | SOXFYTY127E9433E7D | 0.897727807363 |  9   |
| 279292bb36dbfc7f505e36ebf0... | SOYBLYP12A58A79D32 | 0.897092819214 |  10  |
+-------------------------------+--------------------+----------------+------+
[10 rows x 4 columns]